In [21]:
import clingo
import re

In [22]:
def copy_file_content(original_file, new_file):
    with open(original_file, 'r') as src:
        content = src.read()
    with open(new_file, 'w') as dst:
        dst.write(content)

In [47]:
def convert_number_to_words(s):
    num_words = {
        '0': 'zero', '1': 'one', '2': 'two', '3': 'three', '4': 'four',
        '5': 'five', '6': 'six', '7': 'seven', '8': 'eight', '9': 'nine'
    }
    # Replace each digit individually
    return ''.join(num_words.get(char, char) for char in s)

def replace_spaces_with_underscores_in_identifiers(s):
    # Precompile regular expression patterns for performance
    pattern_identifier = re.compile(r'\b([a-z_][a-z0-9_]*)\s+([a-z0-9_]+)\b', re.IGNORECASE)
    
    # Replace spaces between words that are likely part of an identifier with underscores
    def repl(m):
        return m.group(1) + '_' + m.group(2)

    # Apply the replacement repeatedly until no further replacements are made
    while True:
        s_new = pattern_identifier.sub(repl, s)
        if s_new == s:
            break
        s = s_new

    return s

def remove_unnecessary_characters(s):
    # First, remove specified unnecessary characters, keeping the dash to handle it separately
    s = re.sub(r'[\'`*<>~%$‘’"é£á^&#ē|@ü+/]', '', s)
    # Replace "-" with "_", but avoid replacing it within " :- "
    # This uses a negative lookbehind and lookahead to ensure we don't replace dashes in " :- "
    s = re.sub(r'(?<!:)-', '_', s)  # Replace "-" with "_" if "-" is not immediately preceded by ":"
    s = re.sub(r'-(?! )', '_', s)  # Replace "-" with "_" if "-" is not immediately followed by a space, handling the case after ":-"
    
    return s

def remove_all_but_final_period(line):
    # Temporarily replace ":-" with a placeholder
    placeholder = "TEMP_COLON_HYPHEN"
    line = line.replace(':-', placeholder)

    # Remove all periods except the final one if it exists
    parts = line.rsplit('.', 1)
    if len(parts) == 2:
        line = parts[0].replace('.', '') + '.' + parts[1]
    else:
        line = parts[0].replace('.', '')

    # Restore ":-"
    line = line.replace(placeholder, ':-')
    return line

def filter_equals_except_special_cases(s):
    # This approach tries to preserve "=" in logical expressions and assignments
    # by focusing on removing "=" only when it seems to be used in a context that
    # should be filtered out, without a clear-cut method to distinguish all cases accurately.

    # Remove "=" only if it's not clearly part of an assignment or comparison
    # The regex below is an example and might need adjustments
    # It assumes "=" to remove is surrounded by words (identifiers) without spaces
    # This might not cover all cases and could remove "=" in unintended contexts
    s = re.sub(r'(?<=[a-zA-Z0-9_])=(?=[a-zA-Z0-9_])', '', s)
    return s

def filter_colons_except_negations(s):
    # This replaces ":" with "" only if it's not followed by "-", effectively removing colons that are not part of ":-"
    s = re.sub(r':(?!\-)', '', s)
    return s

def filter_asp_code(asp_code):
    filtered_lines = []
    seen_lines = set()
    allowed_prefixes_pattern = re.compile(r'\b(neg|pos|relation)\(')

    for line in asp_code.split('\n'):
        # Add the processed line to the set of seen lines
        seen_lines.add(line)
        # Remove Non ASP code parts and special character
        if re.match(r'^\*\*|```asp', line):
            continue
        # Skip lines based on the new condition for the presence of "not"
        if re.search(r'\bnot\b', line):
            continue 

        # Remove lines not in ASP format
        if not re.match(r'^[a-zA-Z0-9_].*', line):
            continue
        # Convert all numeric digits to their corresponding words
        line = convert_number_to_words(line)
        # Replace spaces with underscores in identifiers
        line = replace_spaces_with_underscores_in_identifiers(line)
        # remove lines with the word section in it
        if "section" in line.lower():
            continue
        if not "." in line.lower():
            continue
        if not allowed_prefixes_pattern.search(line):  # Skip lines not matching the allowed patterns
            continue
        # # Delete incomplete sentences
        # if not re.search(r'\)$', line):
        #     continue
        # Add missing full stops
        if not re.search(r'\.$', line) and re.search(r'\)$', line):
            line += '.'
        # Remove dots between words
        line = re.sub(r'(?<=\w)\.(?=\w)', '', line)
        # remove ! between words
        line = re.sub(r'(?<=\w)\!(?=\w)', '', line)
        # remove special characters
        line = remove_unnecessary_characters(line)
        # Lowercase conversion while keeping ASP keywords or variables intact
        line = re.sub(r'(?<![A-Z])([A-Z]+)(?![A-Z])', lambda x: x.group(1).lower(), line)
        # Ensure only the final period is kept
        line = remove_all_but_final_period(line) 
        line = filter_colons_except_negations(line)
        line = filter_equals_except_special_cases(line)
        # Replace spaces with underscores in identifiers
        line = replace_spaces_with_underscores_in_identifiers(line)
        # line = filter_equals_except_special_cases(line) 
        filtered_lines.append(line)
    return '\n'.join(filtered_lines)
        

def apply_filter_to_asp_code(asp_code_file, output_file):
    with open(asp_code_file, 'r') as file:
        asp_code = file.read()

    filtered_code = filter_asp_code(asp_code)

    with open(output_file, 'w') as file:
        file.write(filtered_code)
    
    print(f"Filtered ASP code has been written to {output_file}")

In [24]:
def clingo_compiling_check(file):
    # Clingo program
    program = clingo.Control()
    # Reading ASP code
    with open(file, 'r') as f:
        asp_code = f.read()
    # Load ASP code
    program.add('base', [], asp_code)
    # Compiling and solving
    try:
        program.ground([("base", [])])
        program.solve()
        return True
    except Exception as e:
        # Returns False if the ASP code has a wrong syntax and is not compiling
        return False

In [25]:
def solve_asp(file_path):
    # Read the ASP code from the file
    with open(file_path, 'r', encoding='utf-8') as file:
        asp_code = file.read()

    # Create a new clingo Control object
    solver = clingo.Control()
    
    # Add the ASP code to the solver
    solver.add("base", [], asp_code)
    
    # Ground the program
    solver.ground([("base", [])])
    
    # Define the on_model function to print models
    def on_model(model):
        print(f"Solution: {model}")
    
    # Solve the ASP program, calling on_model for each solution
    result = solver.solve(on_model=on_model)
    
    # Check if a solution exists
    if result.satisfiable:
        print("A solution exists.")
    else:
        print("No solution exists.")


In [10]:
# copy_file_content("PaLM output.txt", "filtered asp code.txt")

In [48]:
apply_filter_to_asp_code("10000arguments_cmv_asp.txt", "filtered asp code.txt")

Filtered ASP code has been written to filtered asp code.txt


In [12]:
# Apply the filter function on the new file
# filter("filtered asp code.txt")

In [49]:
clingo_compiling_check("filtered asp code.txt")

<block>:145477:16-17: error: syntax error, unexpected )

<block>:309555:5-8: error: syntax error, unexpected not, expecting ) or ;

<block>:309581:37-40: error: syntax error, unexpected not, expecting ) or ;

<block>:309582:40-43: error: syntax error, unexpected not, expecting ) or ;

<block>:478492:17-18: error: syntax error, unexpected )

<block>:478518:15-16: error: syntax error, unexpected )

<block>:482277:139-140: error: lexer error, unexpected �

<block>:482277:139-141: error: lexer error, unexpected �

<block>:482277:139-142: error: lexer error, unexpected …

<block>:482277:139-157: error: syntax error, unexpected <IDENTIFIER>



RuntimeError: parsing failed

In [23]:
solve_asp("filtered asp code.txt")

<block>:12195:30-57: info: atom does not occur in any rule head:
  neg(morality_is_subjective)

<block>:12196:23-48: info: atom does not occur in any rule head:
  neg(laws_are_unnecessary)

<block>:25614:19-33: info: atom does not occur in any rule head:
  influence(z,y)

<block>:25616:25-45: info: atom does not occur in any rule head:
  shift_positions(z,y)

<block>:25618:24-43: info: atom does not occur in any rule head:
  bend_positions(z,y)

<block>:25620:19-33: info: atom does not occur in any rule head:
  causality(z,y)

<block>:25622:15-25: info: atom does not occur in any rule head:
  favor(z,y)

<block>:25624:17-29: info: atom does not occur in any rule head:
  similar(z,y)

<block>:25626:16-27: info: atom does not occur in any rule head:
  common(z,y)

<block>:25628:15-25: info: atom does not occur in any rule head:
  money(z,y)

<block>:25630:19-33: info: atom does not occur in any rule head:
  decisions(z,y)

<block>:39296:33-50: info: atom does not occur in any rule head:


Solution: relation(sketchy,debate) relation(sketchy,topic) relation(sketchy,thesis) relation(sketchy,argument) relation(sketchy,interpretation) relation(sketchy,bible) relation(sketchy,old_testament) relation(sketchy,new_testament) relation(sketchy,king_james_version) relation(god,christianity) relation(pro,trolling) relation(pro,objection) relation(pro,clarification) relation(pro,sarcasm) relation(pro,guideline) relation(pro,apology) relation(pro,confusion) relation(pro,trick) relation(pro,tactic) relation(pro,shame) relation(pro,conduct) relation(pro,change) relation(pro,understanding) relation(pro,existence) relation(pro,presentation) relation(pro,time) relation(pro,forfeit) relation(pro,definition) relation(pro,specification) relation(pro,ground_rule) relation(pro,interpretation) relation(pro,christianity_religion) relation(pro,wikipedia_real) relation(pro,new_argument) relation(pro,glorious_demon_ox_god) relation(pro,glorious_demon_ox_more_than_one) relation(pro,christian_god_more